## 上证综指

In [1]:
import sys
import talib as talib
import pandas as pd
import numpy as np
from pyecharts import options as opts
sys.path.append("..") 
from imp import reload
from src.ts_stock import TsStock
from src.chart import Chart

tsStock = TsStock();
chart = Chart();

/Users/david/anaconda3/lib/python3.6/site-packages/tushare/util/upass.py:28: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  return str(df.ix[0]['token'])


In [2]:
keyword = '上证综指'
sma_periods = [8,17,25,99,145]
hs_index = tsStock.get_daily_data(keyword,'20120101','')
hs_index = hs_index[['trade_date','close','open','high','low','vol']]
kdata_datas=np.array(hs_index.loc[:,['open','close','low','high']])
stock_info = tsStock.get_stock_info(keyword);
trade_dates = np.array(hs_index.trade_date)
vols = np.array(hs_index['vol'])
hs_index['sar'] = talib.SAR(hs_index.high, hs_index.low, acceleration=0.02, maximum=0.2)
hs_index['ATR']=talib.ATR(hs_index.high,hs_index.low,hs_index.close,timeperiod=25)
sma_dic= {}
for period in sma_periods:
    name = "SMA" + str(period)
    sma = talib.SMA(np.array(hs_index.close),period)
    sma_dic[name]={}
    sma_dic[name]['name'] = name;
    sma_dic[name]['datas'] = sma.round(2).tolist();
    
sar = {}
sar['down'] = hs_index.loc[hs_index['close'] > hs_index['sar'],['trade_date','sar']]
sar['up'] = (hs_index[hs_index['close'] < hs_index['sar']])[['trade_date','sar']]

hs_index['macd_dif'],hs_index['macd_dem'],hs_index['macd_ocr'] = talib.MACD(hs_index.close,12,26,9)



grid_chart = chart.get_grid(stock_info,trade_dates.tolist(),kdata_datas.tolist(),vols.tolist(),ma_dic = sma_dic)

macd = chart.get_macd_chart(
    trade_dates.tolist(),
    hs_index.macd_dif.to_numpy().round(2).tolist(),
    hs_index.macd_dem.to_numpy().round(2).tolist(),
    (hs_index["macd_ocr"]*2).to_numpy().round(2).tolist()
)

grid_chart.add(
    macd,
    grid_opts=opts.GridOpts(
        pos_left="6%", pos_right="8%", pos_top="75%", height="10%"
    ),
)
grid_chart.add(
    macd,
    grid_opts=opts.GridOpts(
        pos_left="6%", pos_right="8%", pos_top="75%", height="10%"
    ),
)


## 上证综指K线

In [3]:
grid_chart.render_notebook()

## 个股

In [35]:
sma_periods = [8,17,25,99,145,318,453]
keyword = '中信证券'
start_day='20120101'
stock_info=tsStock.get_stock_info(keyword)
hs= tsStock.get_daily_data(keyword,start_day,'')
#hs=hs[['trade_date','close','open','high','low','vol']]
kdatas = np.array(hs.loc[:,['open','close','low','high']])
trade_dates = np.array(hs.trade_date)
vols = np.array(hs['vol'])
hs['sar'] = talib.SAR(hs.high, hs.low, acceleration=0.1, maximum=2)

sma_dic= {}
for period in sma_periods:
    name = "SMA" + str(period)
    sma = talib.SMA(np.array(hs.close),period)
    hs[name] =sma;
    sma_dic[name]={}
    sma_dic[name]['name'] = name;
    sma_dic[name]['datas'] = sma.round(2).tolist();
sar = {}
sar['down'] = hs.loc[hs['close'] > hs['sar'],['trade_date','sar']]
sar['up'] = (hs[hs['close'] < hs['sar']])[['trade_date','sar']]
hs['bol_up'], hs['bol_mi'], hs['bol_lo'] = talib.BBANDS(hs.close, 17, 2, 2)

grid_chart= chart.get_grid(
    stock_info,
    trade_dates.tolist(), 
    kdatas.tolist(),
    vols.tolist(), 
    ma_dic = sma_dic,
    sar=sar,
    bol=hs[['trade_date','bol_up','bol_mi','bol_lo']] 
)
    
hs['macd_dif'],hs['macd_dem'],hs['macd_ocr'] = talib.MACD(hs.close,12,26,9)

hs['ADOSC'] = talib.ADOSC(hs.high, hs.low, hs.close, hs.vol, fastperiod=3, slowperiod=10)

macd = chart.get_macd_chart(
    trade_dates.tolist(),
    hs.macd_dif.to_numpy().round(2).tolist(),
    hs.macd_dem.to_numpy().round(2).tolist(),
    (hs["macd_ocr"]*2).to_numpy().round(2).tolist()
)

turnover_chart = chart.get_turnover_chart(hs)

adosc_chart = chart.get_adosc_chart(hs)

grid_chart.add(
    adosc_chart,
    grid_opts=opts.GridOpts(
        pos_left="6%", pos_right="8%", pos_top="75%", height="10%"
    ),
)
grid_chart.add(
    turnover_chart,
    grid_opts=opts.GridOpts(
        pos_left="6%", pos_right="8%", pos_top="65%", height="10%"
    ),
)


/Users/david/anaconda3/lib/python3.6/site-packages/tushare/util/upass.py:28: FutureWarning: 
.ix is deprecated. Please use
.loc for label based indexing or
.iloc for positional indexing

See the documentation here:
http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#ix-indexer-is-deprecated
  return str(df.ix[0]['token'])


## k

In [36]:
grid_chart.render_notebook()

In [32]:
close50 = hs.close.shift(50) 

In [22]:
(hs.close - close50 )/close50

trade_date
2012-01-04         NaN
2012-01-05         NaN
2012-01-06         NaN
2012-01-09         NaN
2012-01-10         NaN
                ...   
2019-10-15    0.229349
2019-10-16    0.215976
2019-10-17    0.174853
2019-10-18    0.141748
2019-10-21    0.017652
Name: close, Length: 1430, dtype: float64

In [23]:
hs= tsStock.get_daily_data(keyword,start_day,'')

In [24]:
hs

ts_code trade_date     open     high      low    close  \
trade_date                                                             
2012-01-04  002129.SZ   20120104   4.7112   4.7471   4.2760   4.3971   
2012-01-05  002129.SZ   20120105   4.2984   4.3702   3.9753   4.0516   
2012-01-06  002129.SZ   20120106   4.0112   4.1055   3.8587   4.0696   
2012-01-09  002129.SZ   20120109   4.0875   4.3253   4.0023   4.3163   
2012-01-10  002129.SZ   20120110   4.3208   4.7426   4.2715   4.7426   
...               ...        ...      ...      ...      ...      ...   
2019-10-15  002129.SZ   20191015  12.9000  13.0000  12.6100  12.6500   
2019-10-16  002129.SZ   20191016  12.6900  12.7300  12.2500  12.3300   
2019-10-17  002129.SZ   20191017  12.3200  12.4300  11.9100  11.9600   
2019-10-18  002129.SZ   20191018  11.9700  12.0700  11.6700  11.7600   
2019-10-21  002129.SZ   20191021  11.7300  11.7400  11.3600  11.5300   

            pre_close  change  pct_chg        vol       amount  turnover_rate  \
trade_date                                                                      
2012-01-04     4.6663 -0.2692  -5.7690   72317.89   73088.7084         1.0004   
2012-01-05     4.3971 -0.3455  -7.8575  105536.31   97340.6566         1.4599   
2012-01-06     4.0516  0.0180   0.4443   55628.03   49399.2414         0.7695   
2012-01-09     4.0696  0.2467   6.0620   69270.05   65209.3710         0.9582   
2012-01-10     4.3163  0.4263   9.8765  153865.82  156176.0333         2.1284   
...               ...     ...      ...        ...          ...            ...   
2019-10-15    13.0400 -0.3900  -2.9908  577147.54  736557.5010         2.1509   
2019-10-16    12.6500 -0.3200  -2.5296  608876.21  755777.7310         2.2692   
2019-10-17    12.3300 -0.3700  -3.0008  705048.97  854377.4230         2.6276   
2019-10-18    11.9600 -0.2000  -1.6722  585166.68  692375.6510         2.1808   
2019-10-21    11.7600 -0.2300  -1.9558  488777.79  562425.4510         1.8216   

            volume_ratio  
trade_date                
2012-01-04          1.29  
2012-01-05          1.73  
2012-01-06          0.79  
2012-01-09          0.96  
2012-01-10          2.08  
...                  ...  
2019-10-15          0.83  
2019-10-16          0.93  
2019-10-17          1.04  
2019-10-18          0.90  
2019-10-21          0.76  

[1430 rows x 13 columns]

In [25]:
hs.loc['20120306']

ts_code          002129.SZ
trade_date        20120306
open                6.1066
high                6.2816
low                 6.0707
close               6.2681
pre_close           6.1739
change              0.0942
pct_chg             1.5258
vol                  72618
amount              100066
turnover_rate       1.0045
volume_ratio          0.89
Name: 2012-03-06 00:00:00, dtype: object

In [11]:
import tushare as ts
token = '36d50a0386e9066b5c79c2de58ea2d3a9b980020041adc910f76bfc7'
ts.set_token(token)
pro = ts.pro_api()
daily_basic = pro.daily_basic(ts_code=stock_info['code'], start_date='20120101', end_date='')
daily_basic.index= pd.to_datetime(daily_basic.trade_date)

In [12]:
daily_basic.loc['20120306']

ts_code trade_date  close  turnover_rate  turnover_rate_f  \
trade_date                                                                
2012-03-06  002129.SZ   20120306  13.97         1.0045           2.5762   

            volume_ratio        pe  pe_ttm      pb      ps  ps_ttm  \
trade_date                                                           
2012-03-06          0.89  103.7363  55.724  5.9449  7.7315  3.9673   

            total_share  float_share  free_share      total_mv       circ_mv  
trade_date                                                                    
2012-03-06   72424.4412   72290.5379  28188.0558  1.011769e+06  1.009899e+06

In [13]:
hs

ts_code trade_date     open     high      low    close  \
trade_date                                                             
2012-01-04  002129.SZ   20120104   4.7112   4.7471   4.2760   4.3971   
2012-01-05  002129.SZ   20120105   4.2984   4.3702   3.9753   4.0516   
2012-01-06  002129.SZ   20120106   4.0112   4.1055   3.8587   4.0696   
2012-01-09  002129.SZ   20120109   4.0875   4.3253   4.0023   4.3163   
2012-01-10  002129.SZ   20120110   4.3208   4.7426   4.2715   4.7426   
...               ...        ...      ...      ...      ...      ...   
2019-10-15  002129.SZ   20191015  12.9000  13.0000  12.6100  12.6500   
2019-10-16  002129.SZ   20191016  12.6900  12.7300  12.2500  12.3300   
2019-10-17  002129.SZ   20191017  12.3200  12.4300  11.9100  11.9600   
2019-10-18  002129.SZ   20191018  11.9700  12.0700  11.6700  11.7600   
2019-10-21  002129.SZ   20191021  11.7300  11.7400  11.3600  11.5300   

            pre_close  change  pct_chg        vol       amount  turnover_rate  \
trade_date                                                                      
2012-01-04     4.6663 -0.2692  -5.7690   72317.89   73088.7084         1.0004   
2012-01-05     4.3971 -0.3455  -7.8575  105536.31   97340.6566         1.4599   
2012-01-06     4.0516  0.0180   0.4443   55628.03   49399.2414         0.7695   
2012-01-09     4.0696  0.2467   6.0620   69270.05   65209.3710         0.9582   
2012-01-10     4.3163  0.4263   9.8765  153865.82  156176.0333         2.1284   
...               ...     ...      ...        ...          ...            ...   
2019-10-15    13.0400 -0.3900  -2.9908  577147.54  736557.5010         2.1509   
2019-10-16    12.6500 -0.3200  -2.5296  608876.21  755777.7310         2.2692   
2019-10-17    12.3300 -0.3700  -3.0008  705048.97  854377.4230         2.6276   
2019-10-18    11.9600 -0.2000  -1.6722  585166.68  692375.6510         2.1808   
2019-10-21    11.7600 -0.2300  -1.9558  488777.79  562425.4510         1.8216   

            volume_ratio  
trade_date                
2012-01-04          1.29  
2012-01-05          1.73  
2012-01-06          0.79  
2012-01-09          0.96  
2012-01-10          2.08  
...                  ...  
2019-10-15          0.83  
2019-10-16          0.93  
2019-10-17          1.04  
2019-10-18          0.90  
2019-10-21          0.76  

[1430 rows x 13 columns]

In [14]:
tsStock.token

'36d50a0386e9066b5c79c2de58ea2d3a9b980020041adc910f76bfc7'

In [15]:
ts.set_token(tsStock.token)

In [16]:
df=tsStock.pro.daily(trade_dates='20191016')

In [17]:
df['sort_num'] = df.close.rank(ascending=0,method='min') / len(df) * 100

In [18]:
df

ts_code trade_date   open   high    low  close  pre_close  change  \
0     300639.SZ   20191021  24.81  25.30  23.02  23.88      24.69   -0.81   
1     300607.SZ   20191021  39.32  39.79  38.75  39.06      39.35   -0.29   
2     300675.SZ   20191021  15.43  15.49  15.22  15.39      15.23    0.16   
3     002873.SZ   20191021  16.38  16.55  15.66  15.88      16.89   -1.01   
4     002871.SZ   20191021  21.30  21.30  20.82  21.03      21.23   -0.20   
...         ...        ...    ...    ...    ...    ...        ...     ...   
3995  600280.SH   20191018   3.17   3.17   3.08   3.10       3.16   -0.06   
3996  600273.SH   20191018  10.21  10.27   9.68   9.80      10.21   -0.41   
3997  600272.SH   20191018   7.91   7.97   7.76   7.79       7.95   -0.16   
3998  600271.SH   20191018  21.34  21.44  20.84  20.85      21.28   -0.43   
3999  600258.SH   20191018  17.58  17.94  17.31  17.42      17.65   -0.23   

      pct_chg        vol      amount  sort_num  
0     -3.2807  100580.62  239247.723    13.250  
1     -0.7370    7600.00   29845.237     5.600  
2      1.0506    7323.00   11250.808    25.525  
3     -5.9799   28374.45   45447.968    24.375  
4     -0.9421    9383.10   19668.426    16.400  
...       ...        ...         ...       ...  
3995  -1.8987   39913.92   12449.324    93.250  
3996  -4.0157  285850.24  283631.954    44.775  
3997  -2.0126    7122.00    5592.867    55.325  
3998  -2.0207   75797.84  159873.590    16.675  
3999  -1.3031   46412.67   81799.641    20.875  

[4000 rows x 12 columns]